# Topic Modelling mit BERTopic
Projekt "Trier Digital: Wandel sichtbar machen"

Python 3.10.9

# Vorbereitung: Importe, Laden und Überprüfen der Texte

In [1]:
#Imports

import os
import re
import numpy as np
import pandas as pd
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer, util
from sklearn.feature_extraction.text import CountVectorizer
from umap import UMAP
from nltk.corpus import stopwords
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime


In [2]:
# Pfad zum Korpus (ggf. anpassen im Falle abweichender Ordnerstrukturen o.Ä.)
working_dir = "aufgeteilte_articles"

# Funktion: Texte aus Unterordnern laden inkl. Partei und Datum
def load_texts(directory):
    texts = []
    parties = []
    dates = []

    # Über alle Partei(unter)ordner im Directory iterieren
    for party_name in os.listdir(directory):
        party_path = os.path.join(directory, party_name)

        # Sicherstellen, dass es sich um einen Ordner handelt (falls nicht wird die Iteration übersprungen)
        if not os.path.isdir(party_path):
            continue
        
        # Über alle Dateien im jeweiligen Parteienordner iterieren
        for file in os.listdir(party_path):
            if file.endswith(".txt"):
                file_path = os.path.join(party_path, file)
                with open(file_path, "r", encoding="utf-8") as f:
                    texts.append(f.read().strip())
                    parties.append(party_name)  # Parteinamen hinzufügen

                    # Datum aus Dateinamen extrahieren
                    match = re.search(r'_(\d{4}-\d{2}-\d{2})\.txt$', file)
                    if match:
                        dates.append(datetime.strptime(match.group(1), '%Y-%m-%d'))  # Datum als datetime hinzufügen 
                    else:
                        dates.append(None)  # Andernfalls None hinzufügen

    return texts, parties, dates

# Texte, Parteien und Daten laden
texts, parties, dates = load_texts(working_dir)

# Prüfe, ob Texte geladen wurden
#print(len(texts))
if len(texts) == 0:
    raise ValueError("Fehler - keine Texte gefunden")

In [3]:
# Länge der Texte in Wörtern berechnen, um Eignung für BERTopic zu prüfen
word_lengths = [len(text.split()) for text in texts]

print("Anzahl der Texte:", len(texts))
print("Durchschnittliche Länge (Wörter):", sum(word_lengths) / len(word_lengths))
print("Maximale Länge (Wörter):", max(word_lengths))


Anzahl der Texte: 4642
Durchschnittliche Länge (Wörter): 217.97457992244722
Maximale Länge (Wörter): 367


# Erstellen des Modells

In [36]:
%%time
model_embedding = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2") # Laden des vortrainierten Embedding-Modells
corpus_embeddings = model_embedding.encode(texts) # Berechnung der Embeddings für die Texte im Korpus

# Vorberechnen der Embeddings - dieser Schritt kann eine Weile dauern!

CPU times: user 48min 12s, sys: 4min 43s, total: 52min 55s
Wall time: 8min 46s


In [5]:
# Zum Entfernen von Stoppwörtern

# Laden der deutschen Stoppwortliste aus NLTK
german_stop_words = stopwords.words('german')

# Erstellung eines CountVectorizer-Modells, das deutsche Stopwörter ausschließt
vectorizer_model = CountVectorizer(stop_words = german_stop_words)

In [101]:
%%time

# Instanziierung  und Trainieren des BERTopic-Modells mit spezifischen Parametern
model = BERTopic(
    n_gram_range=(1, 2),  # erlaubt 1 bis 2-Wort-N-Grams
    vectorizer_model=vectorizer_model,  # zuvor definierter CountVectorizer
    language="german",  # Setzt die Sprache auf Deutsch
    #nr_topics="auto",       # Anzahl der Topics
    min_topic_size=20,  # Minimale Größe (= Anzahl von Dokumenten) für ein Topic
    calculate_probabilities=True # Berechnet die Topic-Zuordnungswahrscheinlichkeiten für jedes Dokument
    ).fit(texts, corpus_embeddings)  # Modell mit den Texten und Embeddings trainieren


CPU times: user 18.2 s, sys: 718 ms, total: 19 s
Wall time: 6.96 s


In [106]:
# Modell speichern

output_dir = "bertopic_results"
os.makedirs(output_dir, exist_ok=True)
model.save(f"{output_dir}/bertopic_model")
model.get_topic_info().to_csv(f"{output_dir}/topic_info.csv", index=False)

2025-02-12 11:28:34,708 - BERTopic - WARNING: When you use `pickle` to save/load a BERTopic model,please make sure that the environments in which you saveand load the model are **exactly** the same. The version of BERTopic,its dependencies, and python need to remain the same.


In [245]:
# Über diese Funktion kann das Modell, wenn es gespeichert ist, ggf. geladen werden
model = BERTopic.load(f"{output_dir}/bertopic_model")

In [246]:
# Generieren der vorhergesagten Topics und der Zuordnungswahrscheinlichkeiten für die Dokumente

topics, probabilities = model.transform(texts, corpus_embeddings)


# Prüfen und Überarbeiten des Modells

Für das Checken des Modells sind auch die Visualisierungen hilfreich, vor allem die Grafik "Documents and Topics", mit der ein Blick in die Dokumente jedes Topics geworfen werden kann - siehe dafür unten.

In [247]:
# Funktion für einen Topic-Überblick 

def get_topic_overview(model, topics):
    """
    Gibt einen Überblick über die Topics, einschließlich der zugehörigen Wörter und der Anzahl der zugeordneten Dokumente.

    Parameters:
    - model: Das trainierte BERTopic-Modell.
    - topics: Die Topic-Zuweisungen für die Texte.

    Returns:
    - topic_counts: Ein DataFrame mit den Topics, deren Wörter und der Anzahl der zugeordneten Dokumente.
    - total_docs: Die Gesamtanzahl der Dokumente.
    """
    # DataFrame für Topics und deren Häufigkeit erstellen
    topic_df = pd.DataFrame({'Topic': topics})

    # Anzahl der Dokumente pro Topic zählen
    topic_counts = topic_df['Topic'].value_counts(dropna=False).reset_index()
    topic_counts.columns = ['Topic', 'Count']

    # Wörter für jedes Topic abrufen
    topic_words = {topic: ", ".join([word for word, _ in model.get_topic(topic)])
                   for topic in topic_counts['Topic']}

    # DataFrame um die Wörter ergänzen
    topic_counts['Words'] = topic_counts['Topic'].map(topic_words)

    # Ausgabe der Topics und ihrer Details
    print(topic_counts)
    
    # Gesamtzahl der Dokumente
    total_docs = topic_counts['Count'].sum()
    print(f"\nSumme Counts bzw. Gesamtanzahl der Dokumente: {total_docs}")



In [248]:
# Überblick über Topics und deren Verteilung
get_topic_overview(model, topics)

    Topic  Count                                              Words
0      -1   1468  trier, stadt, fraktion, mehr, wurde, stadtrat,...
1       0    591  stadtrat, fraktion, trier, cdu, stadt, bürger,...
2       1    283  haushalt, euro, stadt, millionen, kommunen, la...
3       2    251  grundschule, schulen, schule, eltern, schüler,...
4       3    120  theater, theaters, sibelius, tufa, intendant, ...
5       4    111  menschen, flüchtlinge, integration, trier, afd...
6       5    102  wohnraum, wohnungen, wohnen, wohnungsbau, trie...
7       6    100  frauen, gewalt, gender, konvention, männer, is...
8       7     84  kultur, antikenfestspiele, trier, spiele, fest...
9       8     78  mobilitätskonzept, straße, fuß, kreuzung, auto...
10      9     72  polizei, sicherheit, 30, innenstadt, tempo, wo...
11     10     69  kita, familien, eltern, kinder, kitas, kinderb...
12     11     65  ubm, maximini, fraktion, stadtpolitik, unserer...
13     12     63  trier, stadt, wirtschaft, wirt

In [249]:
# Mergen von Topics 0 und 11 sowie 7 und 43
topics_to_merge = [[0, 11], [7, 43]]  # Liste der Topic-Paare, die zusammengeführt werden sollen

# Topics zusammenführen
model.merge_topics(texts, topics_to_merge)

# Überschreiben der Variablen mit den neuen Topic-Zuweisungen und den vorab berechneten Embeddings
topics, probabilities = model.transform(texts, embeddings=corpus_embeddings)

# Ausgabe der neuen Topics
get_topic_overview(model, topics)


    Topic  Count                                              Words
0      -1   1468  trier, stadt, fraktion, mehr, wurde, stadtrat,...
1       0    656  ubm, fraktion, stadtrat, trier, stadt, cdu, bü...
2       1    283  haushalt, euro, stadt, millionen, kommunen, la...
3       2    251  grundschule, schulen, schule, eltern, schüler,...
4       3    120  theater, theaters, sibelius, tufa, intendant, ...
5       4    111  menschen, flüchtlinge, integration, trier, afd...
6       5    104  kultur, trier, antikenfestspiele, stadt, trier...
7       6    102  wohnraum, wohnungen, wohnen, wohnungsbau, trie...
8       7    100  frauen, gewalt, gender, konvention, männer, is...
9       8     78  mobilitätskonzept, straße, fuß, kreuzung, auto...
10      9     72  polizei, sicherheit, 30, innenstadt, tempo, wo...
11     10     69  kita, familien, eltern, kinder, kitas, kinderb...
12     11     63  trier, stadt, wirtschaft, wirtschaftsförderung...
13     12     63  innenstadt, einzelhandel, city

In [264]:
def get_topic_overview_with_labels(model, topics):
    """
    Gibt einen Überblick über die Topics, einschließlich der zugehörigen Wörter, der Anzahl der zugeordneten Dokumente
    und der Labels der Topics.

    Parameters:
    - model: Das trainierte BERTopic-Modell.
    - topics: Die Topic-Zuweisungen für die Texte.

    Returns:
    - topic_counts: Ein DataFrame mit den Topics, deren Labels, Anzahl der zugeordneten Dokumente und den Wörtern.
    - total_docs: Die Gesamtanzahl der Dokumente.
    """
    # DataFrame für Topics und deren Häufigkeit erstellen
    topic_df = pd.DataFrame({'Topic': topics})

    # Anzahl der Dokumente pro Topic zählen
    topic_counts = topic_df['Topic'].value_counts(dropna=False).reset_index()
    topic_counts.columns = ['Topic', 'Count']

    # Wörter für jedes Topic abrufen
    topic_words = {topic: ", ".join([word for word, _ in model.get_topic(topic)])
                   for topic in topic_counts['Topic']}

    # DataFrame um die Wörter ergänzen
    topic_counts['Words'] = topic_counts['Topic'].map(topic_words)

    # Labels direkt aus dem 'topic_labels' Dictionary zuweisen
    topic_counts['Label'] = topic_counts['Topic'].map(lambda x: topic_labels.get(x, "Unbekannt"))

    # Spaltenreihenfolge ändern, damit 'Label' zwischen 'Topic' und 'Count' kommt
    topic_counts = topic_counts[['Topic', 'Label', 'Count', 'Words']]

    # Ausgabe der Topics und ihrer Details
    print(topic_counts)
    
    # Gesamtzahl der Dokumente
    total_docs = topic_counts['Count'].sum()
    print(f"\nSumme Counts bzw. Gesamtanzahl der Dokumente: {total_docs}")


In [308]:
# Den Topics Labels geben

#topic_labels = model.generate_topic_labels(nr_words=3, topic_prefix=False, word_length=10,separator=", ")

topic_labels = {
    -1: "Keine Zuordnung",
    0: "Politische Prozesse & Arbeit des Stadtrats",
    1: "Haushalt & Finanzen",
    2: "Schulen",
    3: "Theater",
    4: "Migration",
    5: "Kultur, Feste, Veranstaltungen, Kunst",
    6: "Wohnraum",
    7: "Geschlechterpolitik",
    8: "Mobilität",
    9: "Sicherheit",
    10: "Kinder & Familie",
    11: "Wirtschaft Triers",
    12: "Innenstadt, Einzelhandel",
    13: "Exhaus, Schließungen, Sanierungen",
    14: "Weihnachtsgrüße",
    15: "Parken",
    16: "Jüdische Geschichte & Erinnerungskultur",
    17: "Sport (Vereine, Hallen, Plätze)",
    18: "Digitalisierung",
    19: "Pandemie",
    20: "Feuerwehr",
    21: "Vielfalt & Inklusion",
    22: "Radverkehr",
    23: "Senior*innen",
    24: "Klimaschutz",
    25: "Energiepolitik",
    26: "Weihnachtsmarkt",
    27: "Brücken",
    28: "Fernverkehr, Bahn",
    29: "Neujahr",
    30: "Mosel & Südbad",
    31: "Karl Marx",
    32: "Städtisches Grün",
    33: "Müllpolitik",
    34: "Sportwettkämpfe & Meisterschaften",
    35: "Tourismus",
    36: "Jugendparlament",
    37: "Petrisberg",
    38: "Sommerpause & -grüße",
    39: "Tiere",
    40: "VRT, ÖPNV",
    41: "Flächennutzung"
}

model.set_topic_labels(topic_labels)

topics, probabilities = model.transform(texts, embeddings=corpus_embeddings)

# Ausgabe der neuen Topics mit Labels
get_topic_overview_with_labels(model, topics)



    Topic                                       Label  Count  \
0      -1                             Keine Zuordnung   1468   
1       0  Politische Prozesse & Arbeit des Stadtrats    656   
2       1                         Haushalt & Finanzen    283   
3       2                                     Schulen    251   
4       3                                     Theater    120   
5       4                                   Migration    111   
6       5       Kultur, Feste, Veranstaltungen, Kunst    104   
7       6                                    Wohnraum    102   
8       7                         Geschlechterpolitik    100   
9       8                                   Mobilität     78   
10      9                                  Sicherheit     72   
11     10                            Kinder & Familie     69   
12     11                           Wirtschaft Triers     63   
13     12                    Innenstadt, Einzelhandel     63   
14     13           Exhaus, Schließungen

In [267]:
# Funktion, um alle Texte für ein bestimmtes Topic auszugeben
def get_texts_for_topic(topic_number, texts, topics):
    # Alle Texte, die dem angegebenen Topic zugeordnet wurden
    topic_texts = [text for text, topic in zip(texts, topics) if topic == topic_number]

    # Ausgabe der Texte mit einem Absatz nach jedem Text
    for i, text in enumerate(topic_texts):
        print(f"Text {i + 1}: {text}\n")  # \n fügt einen Absatz nach jedem Text ein

# Beispiel: Alle Texte, die dem Topic 3 zugeordnet wurden
get_texts_for_topic(3, texts, topics)



Text 1: Erst stirbt die Kultur...
…dann die Demokratie! Unter der Überschrift „Neue Eskalationsstufe: Attacken von Rechtsextremen auf Theater nehmen dramatische Ausmaße an“ berichtete die „Huffington Post“ vom 14. Februar über verbale und körperliche Angriffen, Morddrohungen und sogar einem Bombenanschlag gegen Regisseure und Schauspieler an verschiedenen deutschen Theatern.
Zum Glück sind wir in Trier von solchen Verhältnissen sehr weit entfernt. Aber wir dürfen die Diskussion um die Zukunft des Theaters und auch der Kulturförderung der Stadt insgesamt nicht losgelöst von diesen Entwicklungen führen.
Angriffe auf die Kunstfreiheit sind konstitutives Merkmal einer jeden antidemokratischen Bewegung. Beim populistischen Agieren gegen das Theater geht es manchen Akteuren deshalb nur vordergründig um Geld. In Wahrheit handelt es sich um einen Angriff auf jede Form von Kunst und Kultur, die mit ihrem eindimensionalen völkisch-nationalistischen Weltbild nicht übereinstimmt.
Daher ist es ein 

In [268]:
# Beispielhafte Überprüfung eines Dokuments

doc_index = 0  # Beispiel für das erste Dokument (mit Index 0)
max_prob = np.max(probabilities[doc_index])  # Höchste Wahrscheinlichkeit des Dokuments (gehört zu dem Topic, das zugeordnet wird)
max_prob_index = np.argmax(probabilities[doc_index])  # Index des maximalen Werts (Topic)

topic_words = model.get_topic(max_prob_index)  # Wörter des Topics, das zugeordnet wurde
topic_words_str = ", ".join([word for word, _ in topic_words])  # Wörter als String zusammenfügen

doc_text = texts[doc_index]  # Text des Dokuments

# Ausgabe
print(f"Dokument {doc_index} ist dem Topic {max_prob_index} zugeordnet, mit einer Wahrscheinlichkeit von {max_prob:.2f}.")
print(f"Wörter des Topics: {topic_words_str}")
print(f"Text des Dokuments: {doc_text}")




Dokument 0 ist dem Topic 4 zugeordnet, mit einer Wahrscheinlichkeit von 0.94.
Wörter des Topics: menschen, flüchtlinge, integration, trier, afd, stadt, gesellschaft, unserer, mehr, leben
Text des Dokuments: Lastenausgleich
„Herrgott, schick das Gesindel heim.“ Dies ist kein Ausspruch aus der rechtspopulistischen Ecke, sondern aus einer Schmähschrift von 1947 gegen Flüchtlinge aus den früheren Ostgebieten. Circa 14 Millionen mit Bleiberecht kamen bis 1950 nach Deutschland. Eine Herkulesaufgabe.
Trotz anfänglicher Vorbehalte und Ablehnung, so wie wir sie heute bei einem Teil der Bevölkerung auch erleben, wurde diese Integration gut gemeistert. Historiker sind sich einig: Ohne die damalige Zuwanderung hatte es kein so großes Wirtschaftswunder gegeben. Auch in Trier gab es einen Bauboom: Stadtteile wie Heiligkreuz und Feyen entwickelten sich. Namen wie Sudeten-, Pommern- und Memelstraße zeugen davon. Nun zwingen uns die Flüchtlingsströme wieder zur Bewältigung großer Aufgaben, aber in klei

In [269]:
# Wie sicher ist das Modell bei der Zuordnung der Topics?

# DataFrame mit Topics und deren höchsten Wahrscheinlichkeiten erstellen
df = pd.DataFrame({'Topic': topics, 'Max Probability': np.max(probabilities, axis=1)})

# Überblick über die Verteilung der Haupttopic-Wahrscheinlichkeiten
print(df.describe())

# Wie viele Dokumente liegen über einem bestimmten Schwellenwert?
thresholds = [0.2, 0.4, 0.6, 0.8]
for t in thresholds:
    count = (df['Max Probability'] >= t).sum()
    print(f'Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ {t}: {count}')

             Topic  Max Probability
count  4642.000000      4642.000000
mean      7.040715         0.583044
std      11.108283         0.399416
min      -1.000000         0.000549
25%      -1.000000         0.145958
50%       1.000000         0.729969
75%      12.000000         1.000000
max      41.000000         1.000000
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.2: 3230
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.4: 2771
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.6: 2447
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.8: 2188


In [270]:
# Wie sicher ist das Modell bei der Zuordnung der Topics? Ohne Berücksichtigung von Outlier-Topic -1

# DataFrame mit Topics und deren höchsten Wahrscheinlichkeiten erstellen
df = pd.DataFrame({'Topic': topics, 'Max Probability': np.max(probabilities, axis=1)})

# Dokumente mit Topic -1 ausschließen
df_filtered = df[df['Topic'] != -1]

# Überblick über die Verteilung der Haupttopic-Wahrscheinlichkeiten (ohne -1)
print(df_filtered.describe())

# Wie viele Dokumente liegen über einem bestimmten Schwellenwert?
thresholds = [0.2, 0.4, 0.6, 0.8]
for t in thresholds:
    count = (df_filtered['Max Probability'] >= t).sum()
    print(f'Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ {t}: {count}')


             Topic  Max Probability
count  3174.000000      3174.000000
mean     10.759609         0.777831
std      11.693420         0.321274
min       0.000000         0.017728
25%       1.000000         0.682745
50%       6.000000         0.957064
75%      18.000000         1.000000
max      41.000000         1.000000
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.2: 2779
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.4: 2606
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.6: 2442
Anzahl der Dokumente mit einer Haupttopic-Wahrscheinlichkeit ≥ 0.8: 2188


# Generelle Visualisierungen

In [290]:
# Erstelle den Ordner "Visualisierungen", falls er noch nicht existiert
visualizations_dir = "Visualisierungen"
os.makedirs(visualizations_dir, exist_ok=True)

In [292]:
# Visualisierung der Intertopic Distance Map

fig = model.visualize_topics()
fig.show()
# Speichern der Visualisierung als HTML-Datei
fig.write_html(os.path.join(visualizations_dir, "intertopic_distance_map.html"))

In [364]:
# Visualisierung der Topic Word Scores
fig = model.visualize_barchart(top_n_topics=len(model.get_topics()))  # Alle Topics anzeigen

# Größe anpassen
fig.update_layout(
    width=1400,
    #height=1500
)

# Speichern der Visualisierung als HTML-Datei
fig.write_html(os.path.join(visualizations_dir, "topic_barcharts.html"))
# fig.show()


In [294]:
# Visualisierung der Topics mit den dazugehörigen Dokumenten

reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(corpus_embeddings)
fig = model.visualize_documents(texts, reduced_embeddings=reduced_embeddings)
#fig.show()
# Speichern der Visualisierung als HTML-Datei
fig.write_html(os.path.join(visualizations_dir, "topic_documents.html"))

# Spezifische Visualisierungen

In [356]:
# Erstelle ein DataFrame für Topics und Parteien
topic_party_df = pd.DataFrame({'Topic': topics, 'Party': parties})

# Zähle die Vorkommen jedes Topics pro Partei, ohne das Topic -1
topic_counts = topic_party_df[topic_party_df['Topic'] != -1].groupby(['Party', 'Topic']).size().reset_index(name='Count')

# Definiere eine Farbzuordnung für jede Partei
color_map = {
    'AFD': '#009DE0',          # AfD-Farbe
    'CDU': '#000000',          # CDU-Farbe
    'Die Linken': '#DF007D',    # DIE LINKE-Farbe
    'FDP': '#FFED00',          # FDP-Farbe
    'Die Grünen': '#1FAF12',    # Grüne-Farbe
    'SPD': '#FF0000',          # SPD-Farbe
    'UBT-FWG-UBM': '#003366'   # Dunkelblau für UBT-FWG-UBM
}

# Filtere die Daten, um nur die angegebenen Parteien einzuschließen
topic_counts = topic_counts[topic_counts['Party'].isin(color_map.keys())]

# Erstelle ein Balkendiagramm für alle Parteien
fig = go.Figure()

# Füge einen Balken für jede Partei hinzu
for party in topic_counts['Party'].unique():
    party_data = topic_counts[topic_counts['Party'] == party]
    
    # Erstelle den Hover-Text mit den Topic-Wörtern
    hover_text = []
    for topic in party_data['Topic']:
        words = model.get_topic(topic)  # Hole die Wörter für das Topic
        words_str = ", ".join([word for word, _ in words])  # Erstelle einen String aus den Wörtern
        hover_text.append(f'Topic {topic} ({topic_labels.get(topic, f"Topic {topic}")}): {party_data[party_data["Topic"] == topic]["Count"].values[0]} Erwähnungen<br>Wörter des Topics (parteiunabhängig): {words_str}')

    # Füge den Balken-Trace für die aktuelle Partei hinzu
    fig.add_trace(go.Bar(
        x=party_data['Topic'],
        y=party_data['Count'],
        name=party,
        marker_color=color_map.get(party, '#000000'),  # Verwende die zugeordnete Farbe
        hovertext=hover_text,  # Verwende den Hover-Text mit den Wörtern
        hoverinfo='text',  # Zeige den Hover-Text an
        visible='legendonly'  # Setze die Sichtbarkeit auf 'legendonly'
    ))

# Aktualisiere das Layout der Grafik
fig.update_layout(
    title='Topics nach Parteien',  # Titel der Grafik
    xaxis_title='Topics',          # Titel der x-Achse
    yaxis_title='Häufigkeit des Topics',  # Titel der y-Achse
    barmode='group',  # Setze den Modus auf 'group', damit die Balken nebeneinander angezeigt werden
    xaxis_tickangle=-45,  # Drehe die x-Achsen-Beschriftungen um 45 Grad für bessere Lesbarkeit
    xaxis=dict(
        tickvals=topic_counts['Topic'].unique(),  # Setze die Positionen der Topics
        ticktext=[f"Topic {topic}: {topic_labels.get(topic, f'Topic {topic}')}" for topic in topic_counts['Topic'].unique()],  # Setze die IDs und Labels zusammen
        range=[0, 20]  # Setze den Bereich der x-Achse, um nur die ersten 5 Topics anzuzeigen
    ),
    legend_title_text='Parteien',  # Titel der Legende
    height=800  # Hier wird die Höhe des Diagramms angepasst (z.B. 800 Pixel)
)

# Zeige die Grafik an
fig.show()

# Speichere das Balkendiagramm als HTML-Datei
fig.write_html(os.path.join(visualizations_dir, "Themenverteilung_nach_Partei.html"))





In [357]:
# Erstelle ein DataFrame mit Topics und zugehörigen Jahren
topic_time_df = pd.DataFrame({'Topic': topics, 'Year': [date.year if date else None for date in dates]})

# Entferne Topics ohne zugehöriges Datum und schließe Topic -1 aus
topic_time_df = topic_time_df.dropna()
topic_time_df = topic_time_df[topic_time_df['Topic'] != -1]  # Topic -1 ausschließen

# Stelle sicher, dass die Jahreswerte integer sind
topic_time_df['Year'] = topic_time_df['Year'].astype(int)

# Gruppiere nach Jahr und Topic, um die Häufigkeit zu zählen
topic_trends = topic_time_df.groupby(['Year', 'Topic']).size().reset_index(name='Count')

# Sortiere nach Jahr und Topic, um sicherzustellen, dass die Achsen korrekt dargestellt werden
topic_trends = topic_trends.sort_values(by=['Year', 'Topic'], ascending=[True, True])

# Erstelle eine interaktive Liniendiagramm-Visualisierung mit Plotly Graph Objects
fig = go.Figure()

# Sortiere Topics in numerischer Reihenfolge
sorted_topics = sorted(topic_trends['Topic'].unique())

# Füge für jedes Topic den Trace hinzu und stelle sicher, dass die Reihenfolge korrekt ist
for topic in sorted_topics:
    topic_data = topic_trends[topic_trends['Topic'] == topic]
    
    # Hole die Wörter des Topics
    words = model.get_topic(topic)  # Holt die Wörter für das Topic
    words_str = ", ".join([word for word, _ in words])  # Erstellt eine Wortliste
    # Zeige nur die ersten 5 Wörter in der Legende an (optional)
    legend_words = ", ".join([word for word, _ in words[:5]])

    # Erstelle den Hover-Text
    hover_text = [
    f'Topic {topic} ({topic_labels.get(topic, f"Topic {topic}")}): {count} Erwähnungen in {year}<br>Wörter des Topics (zeitunabhängig): {words_str}'
    for count, year in zip(topic_data['Count'], topic_data['Year'])
    ]

    # Füge den Trace für das aktuelle Topic hinzu
    # Wenn es Topic 0 ist, stelle sicher, dass es sichtbar ist, ansonsten 'legendonly'
    fig.add_trace(go.Scatter(
        x=topic_data['Year'],
        y=topic_data['Count'],
        mode='lines+markers',
        name=f'Topic {topic}: {topic_labels.get(topic, f"Topic {topic}")}',  # ID und Label in der Legende
        hovertext=hover_text,  # Hover-Text mit den Wörtern
        hoverinfo='text',  # Zeige den Text im Hover
        legendgroup=str(topic),  # Gruppiert die Topics in der Legende nach Topic
        visible=True if topic == 0 else 'legendonly'  # Topic 0 ist sofort sichtbar, andere nur in der Legende
    ))

# Aktualisiere das Layout der Visualisierung
fig.update_layout(
    title='Topics im Zeitverlauf',
    xaxis_title='Jahr',
    yaxis_title='Häufigkeit des Topics',
    legend_title_text='Themen',
    template='plotly',  # Kein Dark Theme
    legend_traceorder='normal',  # Sortiert die Legende in der Reihenfolge der Topics
    legend=dict(
        title='Themen',
        traceorder='normal',  # Ordnet die Legende nach Topics
        font=dict(size=10)  # Optionale Anpassung der Schriftgröße der Legende
    )
)

# Zeige die Visualisierung
fig.show()

# Speichern der Visualisierung als HTML-Datei
fig.write_html(os.path.join(visualizations_dir, "Zeitverlauf.html"))


